![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS - S 2013 Pré-natal - Parte 3

## Bibliotecas Utilizadas

In [ ]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [2]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA PNS 2013>")

#conferindo as dimensões (número de linhas e colunas)
dim("<Coloque aqui o nome do arquivo RDATA PNS 2013>")

[1] 222385   1000

## Definição do peso e filtragem de respondentes do questionário

In [3]:
#Selecionando registros válidos para o módulo K e calculando peso amostral - summary de verificação
pns2013.1<- <Coloque aqui o nome do arquivo RDATA> %>% filter(M001==1) 
pns2013.1<-pns2013.1 %>% mutate(peso_morador_selec=((V00291*(60202/145572211))))
pns2013.1<-pns2013.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2013.1$peso_morador_selec)

     Min.   1st Qu.    Median      Mean   3rd Qu.      Max. 
 0.004156  0.243959  0.521557  1.000000  1.147413 31.179597 

## Criação de variáveis dos indicadores

In [4]:
#Desfechos - Indicadores

# 11. Proporção de mulheres que realizaram teste/exame para sífilis durante o pré-natal - S011P.
pns2013.1$S011P <- NA
pns2013.1$S011P[pns2013.1$C006==2 & pns2013.1$C008>=18 & pns2013.1$S001==1] <- 2
pns2013.1$S011P[pns2013.1$C006==2 & pns2013.1$C008>=18 & pns2013.1$S001==1 & pns2013.1$S027==1] <- 1
pns2013.1$S011P<-factor(pns2013.1$S011P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$S011P)


# 12. Proporção de mulheres que realizaram teste/exame para sífilis durante o pré-natal e receberam o resultado antes do parto - S012P.

pns2013.1$S012P <- NA
pns2013.1$S012P[pns2013.1$C006==2 & pns2013.1$C008>=18 & pns2013.1$S001==1] <- 2
pns2013.1$S012P[pns2013.1$C006==2 & pns2013.1$C008>=18 & pns2013.1$S001==1 & ( pns2013.1$S028==1 |  pns2013.1$S028==2)] <- 1
pns2013.1$S012P<-factor(pns2013.1$S012P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$S012P)

# 15. Proporção de mulheres que tiveram solicitação de teste/exame para HIV/AIDS durante o pré-natal - S015P.

pns2013.1$S015P <- NA
pns2013.1$S015P[pns2013.1$C006==2 & pns2013.1$C008>=18 & pns2013.1$S001==1] <- 2
pns2013.1$S015P[pns2013.1$C006==2 & pns2013.1$C008>=18 & pns2013.1$S001==1 & pns2013.1$S033 == 1] <- 1
pns2013.1$S015P<-factor(pns2013.1$S015P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$S015P)

Sim   Não  NA's 
 1251   600 58351

Sim   Não  NA's 
 1222   629 58351

Sim   Não  NA's 
 1655   196 58351

## Definições de abrangências

### Situação urbana ou rural

In [5]:
#Situação Urbano ou Rural
pns2013.1 <- pns2013.1 %>% mutate(Sit_Urbano_Rural=V0026)
pns2013.1$Sit_Urbano_Rural<-factor(pns2013.1$Sit_Urbano_Rural, levels=c(1,2), labels=c("urbano", "rural"))
summary(pns2013.1$Sit_Urbano_Rural)

urbano  rural 
 49245  10957

### Sexo

In [6]:
#Sexo
pns2013.1 <- pns2013.1 %>% mutate(Sexo=C006)
pns2013.1$Sexo<-factor(pns2013.1$Sexo, levels=c(1,2), labels=c("Masculino", "Feminino"))
summary(pns2013.1$Sexo)

Masculino  Feminino 
    25920     34282

### UF

In [7]:
#Estados - UFs
pns2013.1 <- pns2013.1 %>% mutate(Unidades_da_Federacao=V0001)
pns2013.1$Unidades_da_Federacao<-factor(pns2013.1$Unidades_da_Federacao, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2013.1$Unidades_da_Federacao)

Rondônia                Acre            Amazonas             Roraima 
               1694                1814                2586                1591 
               Pará               Amapá           Tocantins            Maranhão 
               2004                1332                1515                1774 
              Piauí               Ceará Rio Grande do Norte             Paraíba 
               1804                2560                1691                1943 
         Pernambuco             Alagoas             Sergipe               Bahia 
               2591                1748                1553                2641 
       Minas Gerais      Espírito Santo      Rio de Janeiro           São Paulo 
               3779                1724                3486                5305 
             Paraná      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               3012                1623                2913                1809 
        Mato Grosso               Goiás    Distrito Federal 
               1476                2423                1811

### Grandes Regiões

In [8]:
#Grandes Regiões
pns2013.1 <- pns2013.1 %>% mutate(GrandesRegioes = fct_collapse(Unidades_da_Federacao, 
                                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal")))
summary(pns2013.1$GrandesRegioes)

Norte     Nordeste      Sudeste          Sul Centro-Oeste 
       12536        18305        14294         7548         7519

### Capital

In [9]:
#Capital
pns2013.1<- pns2013.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federacao,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco`= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2013.1$Capital)

Porto Velho     Rio Branco         Manaus      Boa Vista          Belém 
          1694           1814           2586           1591           2004 
        Macapá         Palmas       São Luís       Teresina      Fortaleza 
          1332           1515           1774           1804           2560 
         Natal    João Pessoa         Recife         Maceió        Aracaju 
          1691           1943           2591           1748           1553 
      Salvador Belo Horizonte        Vitória Rio de Janeiro      São Paulo 
          2641           3779           1724           3486           5305 
      Curitiba  Florianópolis   Porto Alegre   Campo Grande         Cuiabá 
          3012           1623           2913           1809           1476 
       Goiânia       Brasília 
          2423           1811

### Faixa Etária

In [10]:
# Faixas Etárias
pns2013.1 <- pns2013.1 %>% mutate(fx_idade_S=cut(C008,
  breaks = c(18,25,30,40,120),
  labels = c("18 a 24 anos", "25 a 29 anos", "30 a 39 anos", "40 anos ou mais"), 
  ordered_result = TRUE, right = FALSE))
summary(pns2013.1$fx_idade_S)

18 a 24 anos    25 a 29 anos    30 a 39 anos 40 anos ou mais 
           7823            6498           14269           31612

### Raça

In [11]:
# Raça
pns2013.1 <- pns2013.1 %>% mutate(Raca= ifelse(C009==1, 1, 
                        ifelse(C009==2, 2, 
                            ifelse(C009==4, 3, 9))))
pns2013.1$Raca<-factor(pns2013.1$Raca, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))
summary(pns2013.1$Raca)

Branca  Preta  Parda   NA's 
 24106   5631  29512    953

### Renda per capita

In [12]:
# Rendimento domiciliar per capita
pns2013.1 <-  pns2013.1 %>% mutate(rend_per_capita=cut(VDF003,
  breaks = c(-Inf,339, 678, 1356, 2034, Inf),
  labels=c("Até 1/2 SM","1/2 até 1 SM","1 até 2 SM","2 até 3 SM","Mais de 3 SM"), 
  ordered_result = TRUE, right = TRUE, na.exclude= TRUE))
summary(pns2013.1$rend_per_capita)

Até 1/2 SM 1/2 até 1 SM   1 até 2 SM   2 até 3 SM Mais de 3 SM         NA's 
       14256        17504        15493         5335         7603           11

### Escolaridade

In [13]:
# Escolaridade
pns2013.1 <- pns2013.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,4
                        ))))
pns2013.1$gescol<-factor(pns2013.1$gescol, levels=c(1,2,3,4), 
                                  labels=c("Fundamental incompleto ou equivalente","Médio incompleto ou equivalente",
                                           "Superior incompleto ou equivalente","Superior completo"))

summary(pns2013.1$gescol)

Fundamental incompleto ou equivalente       Médio incompleto ou equivalente 
                                24083                                  9215 
   Superior incompleto ou equivalente                     Superior completo 
                                19149                                  7755

## Criando indicadores

### Filtrando base de indicadores

In [14]:
# Selecionando variáveis para cálculo de indicadores no survey
pns2013Ssurvey<- pns2013.1 %>% select("V0024","UPA_PNS","peso_morador_selec",  "C008", "C006", "C009", "V0031",
                    "Sit_Urbano_Rural", "Unidades_da_Federacao", "GrandesRegioes",  "Capital", "fx_idade_S", "Raca",
                    "rend_per_capita", "gescol", "S011P", "S012P", "S015P", "S001")  
summary(pns2013Ssurvey)

     V0024            UPA_PNS        peso_morador_selec       C008       
 Min.   :1110011   Min.   :1100001   Min.   : 0.004156   Min.   : 18.00  
 1st Qu.:2210013   1st Qu.:2200075   1st Qu.: 0.243959   1st Qu.: 30.00  
 Median :2951023   Median :2900192   Median : 0.521557   Median : 41.00  
 Mean   :3035353   Mean   :3007819   Mean   : 1.000000   Mean   : 43.31  
 3rd Qu.:4110111   3rd Qu.:4100002   3rd Qu.: 1.147413   3rd Qu.: 55.00  
 Max.   :5310220   Max.   :5300180   Max.   :31.179597   Max.   :101.00  
                                                                         
      C006            C009          V0031       Sit_Urbano_Rural
 Min.   :1.000   Min.   :1.00   Min.   :1.000   urbano:49245    
 1st Qu.:1.000   1st Qu.:1.00   1st Qu.:1.000   rural :10957    
 Median :2.000   Median :3.00   Median :2.000                   
 Mean   :1.569   Mean   :2.61   Mean   :2.308                   
 3rd Qu.:2.000   3rd Qu.:4.00   3rd Qu.:4.000                   
 Max.   :2.000   M

### Exporta tabela filtrada com os dados específicos - Módulo S-Parte3 2013

In [15]:
# Salvando csv para cálculo de indicadores no survey
diretorio_saida <- "<coloque aqui o diretório>"
write.csv(pns2013Ssurvey, file.path(diretorio_saida, "pns2013Ssurvey.csv"))

### Cria plano amostral complexo

In [16]:
# survey design
desPNS=svydesign(id=~UPA_PNS, 
                 strat=~V0024,
                 weight=~peso_morador_selec,
                 nest=TRUE,
                 data=pns2013Ssurvey)

In [17]:
#survey design S011P, S012P e S015P
desPNSS=subset(desPNS,   C006==2 & C008>=18 & S001==1)
desPNSS_C=subset(desPNS, C006==2 & C008>=18 & S001==1 & V0031==1)
desPNSS_R=subset(desPNS, C006==2 & C008>=18 & S001==1 & !is.na(Raca))
desPNSS_Rend=subset(desPNS, C006==2 & C008>=18 & S001==1 & !is.na(rend_per_capita))

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [18]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [19]:
ListaIndicadores = c(~S011P, ~S012P, ~S015P)
ListaIndicadoresTexto = c("S011P", "S012P", "S015P" )
ListaTotais = c('Brasil','Capital')
Ano <- "2013"

In [20]:
ListaDominios = c(~Raca,~rend_per_capita,~fx_idade_S,~Sit_Urbano_Rural,
                      ~Unidades_da_Federacao,~GrandesRegioes,~Capital,~gescol) 
ListaDominiosTexto= c("raça","rend_per_capita","fx_idade_S","urb_rur","uf","região",
                          "capital","gescol") 

#### Preenchendo a tabela de indicadores

In [21]:
#Cálculo dos indicadores usando o pacote survey 
i <- 0
#Para cada indicador
for( indicador in ListaIndicadores){
    i <- i + 1; j <- 1
   
        #Para cada dominio
        for (dominio in ListaDominios){
               #design especifico para capital que é subconjunto do dataframe total
               if (ListaDominiosTexto[j]=="capital"){
                   #designs especificos por variavel que são subconjuntos do dataset total
                   dataframe_indicador<-svyby( indicador , dominio , desPNSS_C , svymean,vartype= c("ci","cv"))
               #Uso design do subconjunto para raça/cor que inclui preta,branca e parda  
               # as outras raças não possuiam dados suficientes para os dominios dos indicadores
               } else if (ListaDominiosTexto[j]=="raça"){
                            dataframe_indicador<-svyby( indicador , dominio , desPNSS_R , svymean,vartype= c("ci","cv"))
               #Udeign específico para renda per capta
               } else if (ListaDominiosTexto[j]=="rend_per_capita"){
                            dataframe_indicador<-svyby( indicador , dominio , desPNSS_Rend , svymean,vartype= c("ci","cv"))    
               #design geral para o subconjunto maior que 18 anos   
               } else {
                        dataframe_indicador<-svyby( indicador , dominio , desPNSS , svymean,vartype= c("ci","cv"))
               }
#União do dataframe de indicadores no formato do painel disponibilizado para PNS
dataframe_indicador<-data.frame(dataframe_indicador)
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Nao","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
    }
}

#### Criando a tabela pela abrangência total

In [22]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [23]:
i=0
for(indicador in ListaIndicadores){
    i <- i+1
    for(total in ListaTotais){
        dataframe_indicador <- data.frame()
        dataframe_indicador_S <- data.frame()
        dataframe_indicador_N <- data.frame()
         if (total == "Capital"){
                   #Indicadores que são subconjunto do dataset total
                            dataframe_indicador <- svymean(indicador,desPNSS_C)
                } else {
                            dataframe_indicador <- svymean(indicador,desPNSS)
                }
        intervalo_confianca <- confint(dataframe_indicador)
        coeficiente_variacao <- cv(dataframe_indicador)
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))
        
        dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        dataframe_indicador_S <- dataframe_indicador %>% 
                                 slice(1)
                
        colnames(dataframe_indicador_S) <- c('Sim','LowerS','UpperS', 'cvS')
        dataframe_indicador_S <- dataframe_indicador_S %>% 
                               select('Sim','LowerS','UpperS','cvS')
        dataframe_indicador_S$Indicador <- ListaIndicadoresTexto[i]
        
        dataframe_indicador_S$abr_tipo <- "total"
        dataframe_indicador_S$abr_nome <- total
        dataframe_indicador_S$Ano <- Ano
        
        dataframe_indicador_S <- dataframe_indicador_S %>% 
                             select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS",'cvS')
        
        matriz_totais <-rbind(matriz_totais,dataframe_indicador_S)
    }
}

In [24]:
matriz_totais

abr_tipo abr_nome Ano  Indicador Sim       LowerS    UpperS   
S011PSim  total    Brasil   2013 S011P     0.6462873 0.6074201 0.6851544
S011PSim1 total    Capital  2013 S011P     0.7459302 0.6968370 0.7950235
S012PSim  total    Brasil   2013 S012P     0.6342498 0.5953764 0.6731232
S012PSim1 total    Capital  2013 S012P     0.7282405 0.6782334 0.7782476
S015PSim  total    Brasil   2013 S015P     0.8909992 0.8676960 0.9143023
S015PSim1 total    Capital  2013 S015P     0.9331653 0.9090692 0.9572614
          cvS       
S011PSim  0.03068382
S011PSim1 0.03357959
S012PSim  0.03127117
S012PSim1 0.03503553
S015PSim  0.01334411
S015PSim1 0.01317468

#### Unindo tabela de indicadores e de totais

In [25]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

#### Visualizando tabela de indicadores

In [26]:
matrizIndicadores

abr_tipo       
Branca                                 raça           
Preta                                  raça           
Parda                                  raça           
Até 1/2 SM                             rend_per_capita
1/2 até 1 SM                           rend_per_capita
1 até 2 SM                             rend_per_capita
2 até 3 SM                             rend_per_capita
Mais de 3 SM                           rend_per_capita
18 a 24 anos                           fx_idade_S     
25 a 29 anos                           fx_idade_S     
30 a 39 anos                           fx_idade_S     
40 anos ou mais                        fx_idade_S     
urbano                                 urb_rur        
rural                                  urb_rur        
Rondônia                               uf             
Acre                                   uf             
Amazonas                               uf             
Roraima                                uf             
Pará                                   uf             
Amapá                                  uf             
Tocantins                              uf             
Maranhão                               uf             
Piauí                                  uf             
Ceará                                  uf             
Rio Grande do Norte                    uf             
Paraíba                                uf             
Pernambuco                             uf             
Alagoas                                uf             
Sergipe                                uf             
Bahia                                  uf             
⋮                                      ⋮              
São Luís2                              capital        
Teresina2                              capital        
Fortaleza2                             capital        
Natal2                                 capital        
João Pessoa2                           capital        
Recife2                                capital        
Maceió2                                capital        
Aracaju2                               capital        
Salvador2                              capital        
Belo Horizonte2                        capital        
Vitória2                               capital        
Rio de Janeiro5                        capital        
São Paulo4                             capital        
Curitiba2                              capital        
Florianópolis2                         capital        
Porto Alegre2                          capital        
Campo Grande2                          capital        
Cuiabá2                                capital        
Goiânia2                               capital        
Brasília2                              capital        
Fundamental incompleto ou equivalente2 gescol         
Médio incompleto ou equivalente2       gescol         
Superior incompleto ou equivalente2    gescol         
Superior completo2                     gescol         
S011PSim                               total          
S011PSim1                              total          
S012PSim                               total          
S012PSim1                              total          
S015PSim                               total          
S015PSim1                              total          
                                       abr_nome                             
Branca                                 Branca                               
Preta                                  Preta                                
Parda                                  Parda                                
Até 1/2 SM                             Até 1/2 SM                           
1/2 até 1 SM                           1/2 até 1 SM                         
1 até 2 SM                             1 até 2 SM                           
2 até 3 SM                             2 até 3 SM                           
Mais de 3 SM 

#### Exportando tabela de indicadores calculados - Módulo S 2013

In [28]:
diretorio_saida <- "<coloque aqui o diretório>"
write.table(matrizIndicadores,file=paste0(diretorio_saida,"Indicadores_2013S_R.csv"),sep = ";",dec = ",",row.names = FALSE)